#                                                                                               Jupyter Notebook to Clean Tweet Data

## Import Packages

In [57]:
import numpy as np 
import pandas as pd 
import re
import matplotlib.pyplot as plt
import nltk
from nltk.sentiment.vader import SentimentIntensityAnalyzer
nltk.download('vader_lexicon')

[nltk_data] Downloading package vader_lexicon to
[nltk_data]     C:\Users\Jordan\AppData\Roaming\nltk_data...


True

## Read In and Clean Data

In [119]:
# Read in original csv from my GitHub
initDataDf = pd.read_csv("https://raw.githubusercontent.com/JordanVencel/DFProject/main/Tesla.csv")
# Filter out tweets that are not in english 
filterDf = initDataDf[['language','tweet']]
filterDf = filterDf.where(filterDf['language'] == 'en')
filterDf = filterDf[filterDf['language'].notna()]
# Grab only tweet text data
tweetDf = filterDf['tweet'].to_frame()
tweetDf = tweetDf.reset_index(drop=True)
# Filter out @s, hashtags, external links, and other irrelavant information using regex
for row in tweetDf.iterrows():
    index = row[0]
    booty = re.sub(r"([@#])\w+", "", row[1][0])
    booty = re.sub(r"(https)([^\s]+)", "", booty)
    booty = re.sub(r"(\?)", "", booty)
    booty = re.sub(r"(.com)", "", booty)
    booty = re.sub(r"([^A-Za-z0-9'!?$\",.\s]*)", "", booty)
    booty = re.sub(r"(^[ \t]+)", "", booty)
    tweetDf.iloc[index][0] = booty

tweetDf

tweet
0     I have six. 4 of them still live at home being...
1     Then go for your dozen kids you are just missi...
2     about buying a country ,   You could turn it i...
3     Actual receipts, and yet you havent asked anyo...
4     Tesla wall battery for the save! Power went ou...
...                                                 ...
7353  Elon Musk liked a tweet from Whole Mars Catalo...
7354  Dude only said he is buying twitter to sell 8 ...
7355                                 Give me your Tesla
7356  Chick Fil A should definitely go public, they ...
7357            Fossil fuels. Like coal, natural gas...

[7358 rows x 1 columns]

In [120]:
# Set up row id formatting for nltk
tweetDf['row_id'] = 0
tweetDf = tweetDf[['row_id', 'tweet']]
for row in tweetDf.iterrows():
    index = row[0]
    newVal = int(index) + 1
    tweetDf['row_id'][index] = newVal

<ipython-input-120-f95b17ada57e>:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tweetDf['row_id'][index] = newVal


## Initialize Sentiment Analysis Dataframe

In [121]:
sentimentDf = pd.DataFrame()
sentimentDf['row_id'] = ['99999999999']
sentimentDf['sentiment_type'] = 'NA999NA'
sentimentDf['sentiment_score'] = 0

print('Processing sentiment analysis...')
sia = SentimentIntensityAnalyzer()
tempDf = sentimentDf
for index, row in tweetDf.iterrows():
    scores = sia.polarity_scores(row[1])
    for key, value in scores.items():
        temp = [key,value,row[0]]
        sentimentDf['row_id'] = row[0]
        sentimentDf['sentiment_type'] = key
        sentimentDf['sentiment_score'] = value
        tempDf = tempDf.append(sentimentDf)
#remove dummy row with row_id = 99999999999
tempDf_cleaned = tempDf[tempDf.row_id != '99999999999']
#remove duplicates if any exist
tempDf_cleaned = tempDf_cleaned.drop_duplicates()
# only keep rows where sentiment_type = compound
tempDf_cleaned = tempDf[tempDf.sentiment_type == 'compound']
print(tempDf_cleaned)



      row_id                                              tweet
0          1  I have six. 4 of them still live at home being...
1          2  Then go for your dozen kids you are just missi...
2          3  about buying a country ,   You could turn it i...
3          4  Actual receipts, and yet you havent asked anyo...
4          5  Tesla wall battery for the save! Power went ou...
...      ...                                                ...
7353    7354  Elon Musk liked a tweet from Whole Mars Catalo...
7354    7355  Dude only said he is buying twitter to sell 8 ...
7355    7356                                 Give me your Tesla
7356    7357  Chick Fil A should definitely go public, they ...
7357    7358            Fossil fuels. Like coal, natural gas...

[7358 rows x 2 columns]
Processing sentiment analysis...


<ipython-input-121-5c42ef3ee944>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  tempDf = tempDf.append(sentimentDf)
<ipython-input-121-5c42ef3ee944>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  tempDf = tempDf.append(sentimentDf)
<ipython-input-121-5c42ef3ee944>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  tempDf = tempDf.append(sentimentDf)
<ipython-input-121-5c42ef3ee944>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  tempDf = tempDf.append(sentimentDf)
<ipython-input-121-5c42ef3ee944>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead

    row_id sentiment_type  sentiment_score
0        1       compound          -0.4767
0        2       compound          -0.5216
0        3       compound           0.5267
0        4       compound           0.5399
0        5       compound           0.3382
..     ...            ...              ...
0     7354       compound           0.4215
0     7355       compound          -0.0516
0     7356       compound           0.0000
0     7357       compound           0.6908
0     7358       compound           0.6124

[7358 rows x 3 columns]


<ipython-input-121-5c42ef3ee944>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  tempDf = tempDf.append(sentimentDf)
<ipython-input-121-5c42ef3ee944>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  tempDf = tempDf.append(sentimentDf)
<ipython-input-121-5c42ef3ee944>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  tempDf = tempDf.append(sentimentDf)
<ipython-input-121-5c42ef3ee944>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  tempDf = tempDf.append(sentimentDf)
<ipython-input-121-5c42ef3ee944>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead

# Analysis Visualization

In [122]:
tempDf_cleaned[["sentiment_score"]].describe()


sentiment_score
count      7358.000000
mean          0.093003
std           0.434962
min          -0.977800
25%          -0.111100
50%           0.000000
75%           0.440400
max           0.982900